In [77]:
import pandas as pd
import numpy as np
import torch
from transformers import BertForQuestionAnswering, BertTokenizer
import numpy as np

In [97]:
def inverse_hamming_distance(s1, s2):
    count = 0
    for i in range(0, len(s1)):
        if s1[i] == s2[i]:
            count += 1
    return count

def scoring_function(x, y):
    if x == "-" or y == "-":
        return -2
    elif x != y:
        return -1
    else:
        return 2

def global_alignment(seq1, seq2, sf):
    """Global sequence alignment using the Needleman–Wunsch algorithm.

    Parameters
    ----------
    seq1: str
        First sequence to be aligned.
    seq2: str
        Second sequence to be aligned.
    scoring_function: Callable

    Returns
    -------
    str
        First aligned sequence.
    str
        Second aligned sequence.
    float
        Final score of the alignment.

    """
    m = len(seq1) + 1
    n = len(seq2) + 1

    # init table
    table = np.ones((m, n)) * np.NINF
    table[0][0] = 0

    for i in range(1, m):
        table[i][0] = table[i - 1][0] + sf(seq1[i - 1], "-")
    for i in range(1, n):
        table[0][i] = table[0][i - 1] + sf("-", seq2[i - 1])

    print(table)

    # table calculation
    for i in range(1, m):
        for j in range(1, n):
            table[i][j] = max(table[i - 1][j - 1] + sf(seq1[i - 1], seq2[j - 1]),
                              table[i - 1][j] + sf(seq1[i - 1], "-"),
                              table[i][j - 1] + sf("-", seq2[j - 1]))

    max_score = table[m - 1][n - 1]
    # trace-back
    alignment1 = ""
    alignment2 = ""
    i = m - 1
    j = n - 1
    while i > 0 or j > 0:
        if i > 0 and j > 0 and table[i][j] == table[i - 1][j - 1] + sf(seq1[i - 1], seq2[j - 1]):
            alignment1 = seq1[i - 1] + alignment1
            alignment2 = seq2[j - 1] + alignment2
            i -= 1
            j -= 1
        elif i > 0 and table[i][j] == table[i - 1][j] + sf(seq1[i - 1], "-"):
            alignment1 = seq1[i - 1] + alignment1
            alignment2 = "-" + alignment2
            i -= 1
        elif j > 0 and table[i][j] == table[i][j - 1] + sf("-", seq2[j - 1]):
            alignment1 = "-" + alignment1
            alignment2 = seq2[j - 1] + alignment2
            j -= 1
        else:
            break

    return alignment1, alignment2, max_score

In [105]:
squad = pd.read_json('..\\data\\dev-slo-v2.0-test.json')
del squad['version']
squad.reset_index()

for _, dset in squad.iterrows():
    for row in dset['data']['paragraphs']:
        context = row['context']
        for qas in row['qas']:
            print(context)
            if('answers' in qas.keys()):
                for ans in qas['answers']:
                    ans_to_find = ans['text']
            if('plausible_answers' in qas.keys()):
                for ans in qas['plausible_answers']:
                    ans_to_find = ans['text']
                    print(ans_to_find)
            print()



Normani (Norman: Nourmands; Francoščina: Normandi; Latinščina: Normanni) so bili ljudje, ki so v 10. in 11. stoletju dali ime Normandiji, regiji v Franciji. Bili so potomci nordijskih ("Norman") napadalcev in piratov iz Danske, Islandije in Norveške, ki so se pod svojim voditeljem Rollom strinjali, da bodo prisegli zvestobo kralju Karlu III. iz Zahodne Frankovske. Skozi generacije asimilacije in mešanja z domačimi frankovskimi in rimsko-gavskimi populacijami so se njihovi potomci postopoma združili s karolinškimi kulturami Zahodne Frankovske. Posebna kulturna in etnična identiteta Normanov se je najprej pojavila v prvi polovici 10. stoletja in se je razvijala v naslednjih stoletjih.

Normani (Norman: Nourmands; Francoščina: Normandi; Latinščina: Normanni) so bili ljudje, ki so v 10. in 11. stoletju dali ime Normandiji, regiji v Franciji. Bili so potomci nordijskih ("Norman") napadalcev in piratov iz Danske, Islandije in Norveške, ki so se pod svojim voditeljem Rollom strinjali, da bodo